In [1]:
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import LeaveOneOut
from sklearn.model_selection import KFold
from sklearn.linear_model import Lasso
from FetusGrowth_BWPrediction import *
from matplotlib import pyplot as plt
import pandas as pd
import numpy as np

In [2]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

from sklearn.exceptions import ConvergenceWarning
ConvergenceWarning('ignore')

sklearn.exceptions.ConvergenceWarning('ignore')

In [3]:
data_df = pd.read_csv('seethapathyCleanedData.csv')
data = getMeasurements_int(data_df)
data = data.drop([i for i in range(len(data['GA'])) if list(data['GA'])[i][1] > 24]).reset_index(drop = True)
data = data.drop([i for i in range(len(data['GA'])) if list(data['GA'])[i][-1] < 27]).reset_index(drop = True)
ml_data = rmMultipleUS(data)
column_toDrop = ['NEONATAL_COMPLICATIONS']

X = ml_data.drop(column_toDrop, axis=1)
y = ml_data['BIRTH_WEIGHT']

In [4]:
def predictParam(df,A_hc,t0_hc,c_hc,A_ac,t0_ac,c_ac,A_bpd,t0_bpd,c_bpd,A_fl,t0_fl,c_fl):
    
    gadel = list(df['GA_AT_DELIVERY'])
    hc = [func(gadel[i], A_hc[i], t0_hc, c_hc) for i in range(len(gadel))]
    ac = [func(gadel[i], A_ac[i], t0_ac, c_ac) for i in range(len(gadel))]
    bpd = [func(gadel[i], A_bpd[i], t0_bpd, c_bpd) for i in range(len(gadel))]
    fl = [func(gadel[i], A_fl[i], t0_fl, c_fl) for i in range(len(gadel))]
    
    df_update = pd.DataFrame(list(zip(hc,ac,bpd,fl,A_hc,A_ac,A_bpd,A_fl)),
               columns =['HC','AC','BPD','FL','A_HC','A_AC','A_BPD','A_FL'])
    return df_update

def CalA_predBiometries(df, t0_hc, c_hc, t0_ac, c_ac, t0_bpd,c_bpd, t0_fl, c_fl,index_ga, cal_ga):
    
    initGA = [df['GA'][i][0:index_ga[i]] for i in range(len(df['GA']))]
    initHC = [df['HC'][i][0:index_ga[i]] for i in range(len(df['HC']))]
    initAC = [df['AC'][i][0:index_ga[i]] for i in range(len(df['AC']))]
    initBPD = [df['BPD'][i][0:index_ga[i]] for i in range(len(df['BPD']))]
    initFL = [df['FL_Rt'][i][0:index_ga[i]] for i in range(len(df['FL_Rt']))]
    
    initA = np.array([100.0 for x in list(df['GA'])])
    
    A_hc_new = cal_A(initA,t0_hc,c_hc,initGA,initHC)
    A_ac_new = cal_A(initA,t0_ac,c_ac,initGA,initAC)
    A_bpd_new = cal_A(initA,t0_bpd,c_bpd,initGA,initBPD)
    A_fl_new = cal_A(initA,t0_fl,c_fl,initGA,initFL)
    
    hc = [func(cal_ga[i], A_hc_new[i], t0_hc, c_hc) for i in range(len(cal_ga))]
    ac = [func(cal_ga[i], A_ac_new[i], t0_ac, c_ac) for i in range(len(cal_ga))]
    bpd = [func(cal_ga[i], A_bpd_new[i], t0_bpd, c_bpd) for i in range(len(cal_ga))]
    fl = [func(cal_ga[i], A_fl_new[i], t0_fl, c_fl) for i in range(len(cal_ga))]
    
    df_update = pd.DataFrame(list(zip(hc,ac,bpd,fl,A_hc_new,A_ac_new,A_bpd_new,A_fl_new)),
               columns =['HC','AC','BPD','FL','A_HC','A_AC','A_BPD','A_FL'])
    
    return df_update

# Birth weight prediction using data upto 24 and 35 Week Prediction

In [5]:
''' Leave one out for birth weight prediction '''

loo = LeaveOneOut()
y_true_list, y_pred_list,fi_coeff_list = [],[],[]
df = pd.DataFrame(columns = ['Alpha', 'Score','BWPredicted24','BWPredicted35','BWActual','Parameter_coeff','intercept'])


i = 0
initt0_hc, initc_hc,initt0_ac, initc_ac,initt0_bpd,initc_bpd,initt0_fl, initc_fl = 15,1,15,1,15,1,15,1
initA_hc = np.ones(len(X)-1)*300; initA_ac = np.ones(len(X)-1)*300
initA_bpd = np.ones(len(X)-1)*100; initA_fl = np.ones(len(X)-1)*100

for train_init_index, test_init_index in loo.split(X):
    
    X_train_init, X_test_init, y_train_init, y_test_init = X.iloc[train_init_index], X.iloc[test_init_index], y.iloc[train_init_index], y.iloc[test_init_index]                           
    A_hc,t0_hc,c_hc, A_ac,t0_ac,c_ac,A_bpd,t0_bpd,c_bpd,A_fl,t0_fl,c_fl = OptimizeVarAllMeasure(X_train_init,
                                                                        initA_hc,initt0_hc, initc_hc,initA_ac,
                                                                        initt0_ac, initc_ac,initA_bpd,initt0_bpd, 
                                                                        initc_bpd,initA_fl,initt0_fl, initc_fl)
    
    initt0_hc, initc_hc,initt0_ac, initc_ac,initt0_bpd,initc_bpd,initt0_fl, initc_fl = t0_hc,c_hc, t0_ac,c_ac,t0_bpd,c_bpd,t0_fl,c_fl
    initA_hc,initA_ac,initA_bpd,initA_fl = A_hc, A_ac, A_bpd, A_fl

    print('\n Optimization done!!')
    X_train_init = X_train_init.reset_index(drop = True)
    y_train_init = y_train_init.reset_index(drop = True)
    
    X_train_init = predictParam(X_train_init,A_hc,t0_hc,c_hc,A_ac,t0_ac,c_ac,A_bpd,t0_bpd,c_bpd,A_fl,t0_fl,c_fl)
    
    y_test_init = y_test_init.reset_index(drop = True)
    X_test_init = X_test_init.reset_index(drop = True)
    
    index_ga24 = [get_count_GALessThan24(x) for x in X_test_init['GA']]
    index_ga35 = [get_count_GALessThan35(x) for x in X_test_init['GA']]
    gaDel = list(X_test_init['GA_AT_DELIVERY'])
    X_test_init24 = CalA_predBiometries(X_test_init, t0_hc, c_hc, t0_ac, c_ac, t0_bpd,c_bpd, t0_fl, c_fl,
                                      index_ga24, gaDel)
    X_test_init35 = CalA_predBiometries(X_test_init, t0_hc, c_hc, t0_ac, c_ac, t0_bpd,c_bpd, t0_fl, c_fl,
                                      index_ga35, gaDel)
            
    #alphas = np.arange(0.006, 0.015, 0.001)
    alphas = [0]
    avg_scores = []

    kf = KFold(n_splits=5, shuffle=True, random_state=10)
    
    for a in alphas:
        scores_lasso = []
        
        for train_index, test_index in kf.split(X_train_init):
            
            X_train, X_test, y_train, y_test = X_train_init.iloc[train_index], X_train_init.iloc[test_index], y_train_init.iloc[train_index], y_train_init.iloc[test_index]
            scores_lasso.append(get_score(Lasso(alpha = a,normalize = True), X_train, X_test, y_train, y_test)[0])
        
        avg_scores.append(round(np.average(scores_lasso),6))
    test_output24 = get_score(Lasso(alpha = alphas[avg_scores.index(max(avg_scores))]), X_train_init, X_test_init24,
                           y_train_init,y_test_init)
    
    test_output35 = get_score(Lasso(alpha = alphas[avg_scores.index(max(avg_scores))]), X_train_init, X_test_init35,
                           y_train_init,y_test_init)
    
    df = df.append({'Alpha' : alphas[avg_scores.index(max(avg_scores))], 'Score': test_output24[0],
                    'BWPredicted24' : test_output24[1],'BWPredicted35': test_output35[1], 'BWActual' : y_test_init, 
                    'Parameter_coeff' : test_output24[2],'intercept' : test_output24[3]},ignore_index = True)
    
    i = i+1
    print(i)
    


 Optimization done!!
1


/home/chandranik/PLOS_code/FetusGrowth_BWPrediction.py:399: UserWarning: With alpha=0, this algorithm does not converge well. You are advised to use the LinearRegression estimator
  model.fit(X_train, y_train)
/home/chandranik/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: UserWarning: Coordinate descent with no regularization may lead to unexpected results and is discouraged.
  model = cd_fast.enet_coordinate_descent(
/home/chandranik/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.591e+01, tolerance: 1.059e-02 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using one of the solvers implemented in sklearn.linear_model.Ridge/RidgeCV instead.
  model = cd_fast.enet_coordina


 Optimization done!!
2


/home/chandranik/PLOS_code/FetusGrowth_BWPrediction.py:399: UserWarning: With alpha=0, this algorithm does not converge well. You are advised to use the LinearRegression estimator
  model.fit(X_train, y_train)
/home/chandranik/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: UserWarning: Coordinate descent with no regularization may lead to unexpected results and is discouraged.
  model = cd_fast.enet_coordinate_descent(
/home/chandranik/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.570e+01, tolerance: 1.053e-02 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using one of the solvers implemented in sklearn.linear_model.Ridge/RidgeCV instead.
  model = cd_fast.enet_coordina


 Optimization done!!
3


...

/home/chandranik/PLOS_code/FetusGrowth_BWPrediction.py:399: UserWarning: With alpha=0, this algorithm does not converge well. You are advised to use the LinearRegression estimator
  model.fit(X_train, y_train)
/home/chandranik/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: UserWarning: Coordinate descent with no regularization may lead to unexpected results and is discouraged.
  model = cd_fast.enet_coordinate_descent(
/home/chandranik/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.304e+01, tolerance: 1.010e-02 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using one of the solvers implemented in sklearn.linear_model.Ridge/RidgeCV instead.
  model = cd_fast.enet_coordina


 Optimization done!!
773


/home/chandranik/PLOS_code/FetusGrowth_BWPrediction.py:399: UserWarning: With alpha=0, this algorithm does not converge well. You are advised to use the LinearRegression estimator
  model.fit(X_train, y_train)
/home/chandranik/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: UserWarning: Coordinate descent with no regularization may lead to unexpected results and is discouraged.
  model = cd_fast.enet_coordinate_descent(
/home/chandranik/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.313e+01, tolerance: 1.008e-02 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using one of the solvers implemented in sklearn.linear_model.Ridge/RidgeCV instead.
  model = cd_fast.enet_coordina


 Optimization done!!
774


/home/chandranik/PLOS_code/FetusGrowth_BWPrediction.py:399: UserWarning: With alpha=0, this algorithm does not converge well. You are advised to use the LinearRegression estimator
  model.fit(X_train, y_train)
/home/chandranik/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: UserWarning: Coordinate descent with no regularization may lead to unexpected results and is discouraged.
  model = cd_fast.enet_coordinate_descent(
/home/chandranik/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.310e+01, tolerance: 1.008e-02 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using one of the solvers implemented in sklearn.linear_model.Ridge/RidgeCV instead.
  model = cd_fast.enet_coordina

In [6]:
df.to_pickle('BWPridiction_LR.pickle')